In [54]:
include("helper.jl")
include("algorithms.jl")
using NPZ
using Plots

In [55]:
Threads.nthreads()

6

# Competition

In [56]:
f(N) = ceil(Int64, 15 * N * log(N))

f (generic function with 1 method)

# Number of iterations tests

In [65]:
@inline function houdayer_mixed_tricks(
        h::Matrix{Float64}, nb::Int64, nb_iter::Int64,
        x_star::Vector{Int8}, a::Float64, b::Float64, adj::BitMatrix, n0::Int64)
        
    overlap_vector = Vector{Float64}(undef, nb_iter)
    
    cur_x1 = generate_x(nb)
    cur_x2 = generate_x(nb)
    
    nb_votes = ceil(Int64, nb_iter * 0.15 * 2500 / nb)
    nb_factor = ceil(Int64, nb_iter * 0.35 * 2500 / nb)
    
    for i = 1:(nb_iter - nb_factor)
        if mod(i, n0) == 0 && (!all(cur_x1 .== cur_x2))
            houdayer_step!(cur_x1, cur_x2, adj, N)
        end
        
        metropolis_step_factor!(h, cur_x1, nb, 1.0)
        metropolis_step_factor!(h, cur_x2, nb, 1.0)
        
        overlap_vector[i] = overlap(cur_x1, x_star)        
    end
    
    for i = (nb_iter - nb_factor + 1):(nb_iter - nb_votes)
        if mod(i, n0) == 0 && (!all(cur_x1 .== cur_x2))
            houdayer_step!(cur_x1, cur_x2, adj, N)
        end
        
        metropolis_step_factor!(h, cur_x1, nb, 2.0)
        metropolis_step_factor!(h, cur_x2, nb, 2.0)
        
        overlap_vector[i] = overlap(cur_x1, x_star)
        
    end
    
    votes1 = Matrix{Int8}(undef, nb, nb_votes)
    votes2 = Matrix{Int8}(undef, nb, nb_votes)
    
    for (idx, i) = enumerate((nb_iter-nb_votes+1):nb_iter)
        if mod(i, n0) == 0 && (!all(cur_x1 .== cur_x2))
            houdayer_step!(cur_x1, cur_x2, adj, N)
        end
        
        metropolis_step_factor!(h, cur_x1, nb, 2.0)
        metropolis_step_factor!(h, cur_x2, nb, 2.0)
        
        overlap_vector[i] = overlap(cur_x1, x_star)
        
        votes1[:, idx] = cur_x1
        votes2[:, idx] = cur_x2
    end
    
    cur_x1 = majority_vote(votes1)
    cur_x2 = majority_vote(votes2)
    
    return hamiltonian(cur_x1, h) < hamiltonian(cur_x2, h) ? cur_x1 : cur_x2, overlap_vector
    
end

houdayer_mixed_tricks (generic function with 1 method)

In [66]:
# Number of nodes in graph
a = 5.9
b = 0.1
n0 = 1000

N = 5000
x_star = generate_x(N)
adj = generate_graph(x_star, a, b)

nb_exp = 5
nb_iter = f(N)

638790

In [ ]:
@time begin
    
    overlap_hat = run_experiment(N, a, b,
        x_star, houdayer_mixed_tricks, nb_iter, nb_exp, n0)
    npzwrite("data/overlap_test_comp_$(N).npy", overlap_hat)
    
end

In [63]:
overlap_hat[end-20:end]

21-element Vector{Float64}:
 0.9137599999999999
 0.9137599999999999
 0.9137599999999999
 0.9139200000000001
 0.9139200000000001
 0.9139200000000001
 0.9139200000000001
 0.9137600000000001
 0.9137600000000001
 0.9137600000000001
 0.9137600000000001
 0.9136000000000001
 0.9136000000000001
 0.9136000000000001
 0.9136000000000001
 0.9136000000000001
 0.9136000000000001
 0.9136000000000001
 0.9134399999999999
 0.9134399999999999
 0.9134399999999999

In [64]:
plot(overlap_hat, legend=:bottomright)

# Runtimes tests

In [ ]:
# Number of nodes in graph
a = 5.9
b = 0.1
n0 = 1000

N = 2500
x_star = generate_x(N)
adj = generate_graph(x_star, a, b)

nb_exp = 6
nb_iter = f(N)

In [ ]:
@time begin

    x_hat_matrix = competition(adj, a, b, nb_iter, nb_exp, N)
    
end